In [ ]:
!bash get_train_data.sh; bash get_train_data.sh; bash get_train_data.sh; bash get_train_data.sh; bash get_train_data.sh

In [ ]:
!bash get_train_data.sh; bash get_train_data.sh; bash get_train_data.sh; bash get_train_data.sh; bash get_train_data.sh

In [ ]:
!cat train-data*.csv > models/20192009_14/train.csv

In [17]:
from xgboost import XGBClassifier
import pandas as pd
import numpy as np
import pickle
from sklearn.neural_network import MLPClassifier
from sklearn.model_selection import train_test_split
from sklearn.linear_model import LogisticRegression
from sklearn.metrics import accuracy_score
from sklearn.ensemble import RandomForestClassifier

In [47]:
!cat models/20192009_14/train.csv | wc -l

3864


In [48]:
!ls models/20192009_14/

train.csv


In [49]:
features = ["f" + str(i) for i in range(0,243)]
label = ["action"]

headers = features + label

df = pd.read_csv('models/20192009_14/train.csv', 
                 sep = ',', 
                 header = None,
                 names = headers)
df

f0  f1  f2  f3  f4  f5  f6  f7  f8  f9  ...  f234  f235  f236  f237  \
0      0   0   0   0   0   0   0   0   0   0  ...     0     0     0     0   
1      4   0   0   0   0   1   0   0   0   0  ...     0     0     0     0   
2      2   0   1   0   0   0   1   0   0   0  ...     0     0     0     0   
3      0   0   0   0   0   0   0   1   0   1  ...     0     0     0     0   
4      4   0   0   0   0   0   0   0   0   0  ...     0     0     0     0   
...   ..  ..  ..  ..  ..  ..  ..  ..  ..  ..  ...   ...   ...   ...   ...   
3860   3   0   0   0   0   0   0   0   0   0  ...     0     0     0     0   
3861   3   0   0   0   0   0   0   0   0   0  ...     0     0     0     0   
3862   3   0   0   0   0   0   0   0   0   0  ...     0     0     0     0   
3863   3   0   0   0   0   0   0   0   1   0  ...     0     0     0     0   
3864   3   0   0   0   0   0   0   0   1   0  ...     0     0     0     0   

      f238  f239  f240  f241  f242  action  
0        0     0     0     0     0       0  
1        0     0     0     0     0       0  
2        0     0     0     0     0       0  
3        0     0     0     0     0       0  
4        0     0     0     0     0       4  
...    ...   ...   ...   ...   ...     ...  
3860     1     0     0     0     0       3  
3861     1     0     0     0     0       3  
3862     1     0     0     0     0       2  
3863     1     0     0     0     0       3  
3864     1     0     0     0     0       2  

[3865 rows x 244 columns]

In [50]:
print("headers length: {}, df lenght: {}".format(len(headers), len(df)))

headers length: 244, df lenght: 3865


In [51]:
df["f0"].value_counts()

1    1304
3    1218
5    1191
0      59
4      47
2      46
Name: f0, dtype: int64

In [52]:
print("different actions count \n{}".format(df.drop_duplicates()['action'].value_counts()))

different actions count 
0    1446
1    1382
4     467
5     435
3      77
2      58
Name: action, dtype: int64


In [53]:
print("no of states without duplicates: {}".format(len(df.drop_duplicates())))

no of states without duplicates: 3865


In [54]:
y_train_all = df["action"]
X_train_all = df.drop(columns="action")

In [55]:
print("no of states without duplicates and action column: {}".format(len(X_train_all.drop_duplicates())))

no of states without duplicates and action column: 3865


In [56]:
import pandas_profiling
pandas_profiling.ProfileReport(df)

In [57]:
# X_train_all[["f0", "f1"]]

In [58]:
def evaluate_model(xtrain, ytrain, xtest, ytest, model):
    y_pred_test = model.predict(xtest)
    y_pred_train = model.predict(xtrain)
    test_accuracy = accuracy_score(ytest, y_pred_test)
    train_accuracy = accuracy_score(ytrain, y_pred_train)
    print('Training accuracy: {0:.2f}, evaluation accuracy: {1:.2f}'.format(train_accuracy, test_accuracy))


Basic logisting regresion

In [59]:
X_train, X_test, y_train, y_test = train_test_split(X_train_all, y_train_all, test_size=0.2)

classifier = LogisticRegression().fit(X_train, y_train)

In [60]:
evaluate_model(X_train, y_train, X_test, y_test, classifier)

Training accuracy: 0.66, evaluation accuracy: 0.60


In [61]:
pickle.dump(classifier, open("ai_model_logit.pkl","wb"))

xgboost

In [62]:
X_train, X_test, y_train, y_test = train_test_split(X_train_all, y_train_all, 
                                                    test_size=0.2, random_state=7)

xgb_model = XGBClassifier(n_estimators=500).fit(X_train, y_train,eval_set = [[X_test, y_test]], verbose = 1)

[0]	validation_0-merror:0.27555
[1]	validation_0-merror:0.284605
[2]	validation_0-merror:0.285899
[3]	validation_0-merror:0.283312
[4]	validation_0-merror:0.284605
[5]	validation_0-merror:0.284605
[6]	validation_0-merror:0.284605
[7]	validation_0-merror:0.284605
[8]	validation_0-merror:0.284605
[9]	validation_0-merror:0.284605
[10]	validation_0-merror:0.284605
[11]	validation_0-merror:0.284605
[12]	validation_0-merror:0.284605
[13]	validation_0-merror:0.284605
[14]	validation_0-merror:0.283312
[15]	validation_0-merror:0.279431
[16]	validation_0-merror:0.278137
[17]	validation_0-merror:0.276843
[18]	validation_0-merror:0.27555
[19]	validation_0-merror:0.269082
[20]	validation_0-merror:0.269082
[21]	validation_0-merror:0.270375
[22]	validation_0-merror:0.271669
[23]	validation_0-merror:0.271669
[24]	validation_0-merror:0.272962
[25]	validation_0-merror:0.272962
[26]	validation_0-merror:0.272962
[27]	validation_0-merror:0.270375
[28]	validation_0-merror:0.270375
[29]	validation_0-merror:0

[238]	validation_0-merror:0.14489
[239]	validation_0-merror:0.14489
[240]	validation_0-merror:0.146184
[241]	validation_0-merror:0.146184
[242]	validation_0-merror:0.143596
[243]	validation_0-merror:0.143596
[244]	validation_0-merror:0.143596
[245]	validation_0-merror:0.143596
[246]	validation_0-merror:0.143596
[247]	validation_0-merror:0.143596
[248]	validation_0-merror:0.143596
[249]	validation_0-merror:0.143596
[250]	validation_0-merror:0.143596
[251]	validation_0-merror:0.143596
[252]	validation_0-merror:0.143596
[253]	validation_0-merror:0.14489
[254]	validation_0-merror:0.14489
[255]	validation_0-merror:0.14489
[256]	validation_0-merror:0.14489
[257]	validation_0-merror:0.14489
[258]	validation_0-merror:0.14489
[259]	validation_0-merror:0.142303
[260]	validation_0-merror:0.142303
[261]	validation_0-merror:0.141009
[262]	validation_0-merror:0.139715
[263]	validation_0-merror:0.138422
[264]	validation_0-merror:0.138422
[265]	validation_0-merror:0.138422
[266]	validation_0-merror:0.

[474]	validation_0-merror:0.098318
[475]	validation_0-merror:0.098318
[476]	validation_0-merror:0.098318
[477]	validation_0-merror:0.098318
[478]	validation_0-merror:0.099612
[479]	validation_0-merror:0.098318
[480]	validation_0-merror:0.098318
[481]	validation_0-merror:0.098318
[482]	validation_0-merror:0.098318
[483]	validation_0-merror:0.098318
[484]	validation_0-merror:0.098318
[485]	validation_0-merror:0.098318
[486]	validation_0-merror:0.098318
[487]	validation_0-merror:0.097025
[488]	validation_0-merror:0.097025
[489]	validation_0-merror:0.097025
[490]	validation_0-merror:0.098318
[491]	validation_0-merror:0.098318
[492]	validation_0-merror:0.098318
[493]	validation_0-merror:0.098318
[494]	validation_0-merror:0.097025
[495]	validation_0-merror:0.097025
[496]	validation_0-merror:0.095731
[497]	validation_0-merror:0.095731
[498]	validation_0-merror:0.095731
[499]	validation_0-merror:0.097025


In [63]:
evaluate_model(X_train, y_train, X_test, y_test, xgb_model)

Training accuracy: 0.98, evaluation accuracy: 0.90


In [64]:
xgb_model = XGBClassifier(n_estimators=500).fit(X_train_all, y_train_all)

In [65]:
pickle.dump(xgb_model, open("ai_model_xgb.pkl","wb"))

random forest model

In [66]:
forest_model = RandomForestClassifier(random_state=1, n_estimators=100)
forest_model.fit(X_train, y_train)

RandomForestClassifier(bootstrap=True, class_weight=None, criterion='gini',
                       max_depth=None, max_features='auto', max_leaf_nodes=None,
                       min_impurity_decrease=0.0, min_impurity_split=None,
                       min_samples_leaf=1, min_samples_split=2,
                       min_weight_fraction_leaf=0.0, n_estimators=100,
                       n_jobs=None, oob_score=False, random_state=1, verbose=0,
                       warm_start=False)

In [67]:
evaluate_model(X_train, y_train, X_test, y_test, forest_model)

Training accuracy: 1.00, evaluation accuracy: 0.70


In [68]:
pickle.dump(forest_model, open("ai_model_forest.pkl","wb"))

In [69]:
# min_max_scaler = MinMaxScaler()
# np_scaled = min_max_scaler.fit_transform(df)
# df_normalized = pd.DataFrame(np_scaled)
# df_normalized.columns = feature_cols + ['Class']

In [70]:
# def make_crosses(X_train, X_validation, degree=2):
#   from sklearn.preprocessing import PolynomialFeatures
#   poly = PolynomialFeatures(degree=degree)
#   X_train_poly = poly.fit_transform(X_train)
#   X_validation_poly = poly.transform(X_validation)
#   return X_train_poly, X_validation_poly

In [71]:
mlp_model = MLPClassifier(solver='adam', alpha=1e-5, 
                    hidden_layer_sizes=(60, 24, 24), 
                          random_state=1, verbose=True)

mlp_model.fit(X_train, y_train)

Iteration 1, loss = 1.50058619
Iteration 2, loss = 1.37782461
Iteration 3, loss = 1.33188126
Iteration 4, loss = 1.29642021
Iteration 5, loss = 1.26621188
Iteration 6, loss = 1.23575061
Iteration 7, loss = 1.20616291
Iteration 8, loss = 1.16880521
Iteration 9, loss = 1.12607111
Iteration 10, loss = 1.07045593
Iteration 11, loss = 1.01153201
Iteration 12, loss = 0.93256501
Iteration 13, loss = 0.85048052
Iteration 14, loss = 0.77088771
Iteration 15, loss = 0.69421014
Iteration 16, loss = 0.63990360
Iteration 17, loss = 0.59288565
Iteration 18, loss = 0.55637136
Iteration 19, loss = 0.51625461
Iteration 20, loss = 0.48386642
Iteration 21, loss = 0.45281375
Iteration 22, loss = 0.43578896
Iteration 23, loss = 0.40000261
Iteration 24, loss = 0.37749930
Iteration 25, loss = 0.35135682
Iteration 26, loss = 0.32777546
Iteration 27, loss = 0.30519753
Iteration 28, loss = 0.28452123
Iteration 29, loss = 0.27014918
Iteration 30, loss = 0.24770628
Iteration 31, loss = 0.23238780
Iteration 32, los

MLPClassifier(activation='relu', alpha=1e-05, batch_size='auto', beta_1=0.9,
              beta_2=0.999, early_stopping=False, epsilon=1e-08,
              hidden_layer_sizes=(60, 24, 24), learning_rate='constant',
              learning_rate_init=0.001, max_iter=200, momentum=0.9,
              n_iter_no_change=10, nesterovs_momentum=True, power_t=0.5,
              random_state=1, shuffle=True, solver='adam', tol=0.0001,
              validation_fraction=0.1, verbose=True, warm_start=False)

In [72]:
evaluate_model(X_train, y_train, X_test, y_test, mlp_model)

Training accuracy: 1.00, evaluation accuracy: 0.80


In [73]:
mlp_model = MLPClassifier(solver='adam', alpha=1e-5, 
                    hidden_layer_sizes=(24, 24, 24), 
                          random_state=1, verbose=True, max_iter=1000)

mlp_model.fit(X_train_all, y_train_all)

Iteration 1, loss = 1.46531742
Iteration 2, loss = 1.37350709
Iteration 3, loss = 1.34161298
Iteration 4, loss = 1.31175256
Iteration 5, loss = 1.28868364
Iteration 6, loss = 1.26016940
Iteration 7, loss = 1.23818989
Iteration 8, loss = 1.21053782
Iteration 9, loss = 1.18227314
Iteration 10, loss = 1.15332230
Iteration 11, loss = 1.12224540
Iteration 12, loss = 1.09204936
Iteration 13, loss = 1.05764201
Iteration 14, loss = 1.01904391
Iteration 15, loss = 0.97132700
Iteration 16, loss = 0.92217958
Iteration 17, loss = 0.87397774
Iteration 18, loss = 0.82880857
Iteration 19, loss = 0.78581814
Iteration 20, loss = 0.75065951
Iteration 21, loss = 0.71624803
Iteration 22, loss = 0.68686102
Iteration 23, loss = 0.66480643
Iteration 24, loss = 0.63818508
Iteration 25, loss = 0.61570778
Iteration 26, loss = 0.60043738
Iteration 27, loss = 0.58035023
Iteration 28, loss = 0.55099347
Iteration 29, loss = 0.53702016
Iteration 30, loss = 0.51735116
Iteration 31, loss = 0.49732281
Iteration 32, los

MLPClassifier(activation='relu', alpha=1e-05, batch_size='auto', beta_1=0.9,
              beta_2=0.999, early_stopping=False, epsilon=1e-08,
              hidden_layer_sizes=(24, 24, 24), learning_rate='constant',
              learning_rate_init=0.001, max_iter=1000, momentum=0.9,
              n_iter_no_change=10, nesterovs_momentum=True, power_t=0.5,
              random_state=1, shuffle=True, solver='adam', tol=0.0001,
              validation_fraction=0.1, verbose=True, warm_start=False)

Save models to pkl

In [74]:
pickle.dump(mlp_model, open("ai_model_mlp.pkl","wb"))

In [76]:
!bash evaluate-ai.sh

evaluation of logit
evaluation logit with 10 attempts, resulted with, avg time: 1.5 and avg score: 0.2
evaluation of xgb
evaluation xgb with 10 attempts, resulted with, avg time: 1.7 and avg score: 2.6
evaluation of mlp
evaluation mlp with 10 attempts, resulted with, avg time: 4.5 and avg score: 21.1333
evaluation of forest
evaluation forest with 10 attempts, resulted with, avg time: 2.2 and avg score: 0.1


In [ ]:
# model_p = pickle.load(open("ai_model.pkl","rb"))
game_state_4f = (np.array([8,280,630,-1,1,674,-3,7,667,-1,2,649,-3,2,662,0,3,662,-1,4,655,-1,5,608,2,7,1,8,288,630,-1,1,672,-3,7,668,-1,2,650,-3,2,661,0,3,657,-1,4,649,-1,5,602,2,7,1,8,296,629,-1,1,670,-3,7,669,-1,2,651,-3,2,660,0,3,651,-1,4,643,-1,5,596,2,7,1,8,296,628,-1,1,665,-3,7,667,-1,2,650,-3,2,658,0,3,647,-1,4,638,-1,5,589,2,7])
                 .reshape(1, -1))

game_state_1f = (np.array([25, -410, 308, 5, 1, -343, 483, 1, 2, -417, 592, 5, 2, -184, 589, 1, 2, -222, 275, 7, 2, -93, 143, 3, -2, -128, 549, 1, -3, -121, 399, 6, -3]).reshape(1, -1))

xgb_model.predict(game_state_1f)